# PID Control 

You'll learn how a PID (Proportional-Integral-Derivative) controller works, write your own controller, and tune its parameters interactively.

---

## What is a PID Controller?

A PID controller calculates an error value as the difference between a desired setpoint and a measured process variable.

**PID Formula**:
$$
u(t) = K_p e(t) + K_i \int_0^t e(\tau)d\tau + K_d \frac{de(t)}{dt}
$$

Where:
- **Kp**: Proportional gain
- **Ki**: Integral gain
- **Kd**: Derivative gain
- **e(t)**: Error = Setpoint - Current Value

You’ll see how changing Kp, Ki, and Kd affects the system.


# Resources
You must watch at least the fist 4 videos of this Youtube playlist

https://www.youtube.com/playlist?list=PLn8PRpmsu08pQBgjxYFXSsODEF3Jqmm-y

# Instructions

- The code provided is to implement PID control on the thrust of a drone to make it reach a target height.

- There are incomplete code blocks and statements in the notebook which you must complete.

- You are expected to watch the videos provided and NOT refer to chatgpt for this checkpoint as it is not required.

- The goal of this assignment is to understand how a pid controller works intuitively and see how each term affects your controller.

- The code will work properly only if the missing code blocks are correctly filled

In [86]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML

class Drone:
    def __init__(self):
        self.height = 0.0
        self.velocity = 0.0

    def update(self, thrust, dt):
        gravity = -9.81    
        mass = 1.0
        acceleration = (thrust / mass) + gravity
        self.velocity += acceleration * dt
        self.height += self.velocity * dt
        return self.height

class PIDController:
    def __init__(self, Kp, Ki, Kd):
        self.Kp = Kp
        self.Ki = Ki
        self.Kd = Kd
        # you might need to add more variables here... hint: for Integral controller
        self.accumulatedintegral = 0

    def update(self, error, dt,error2):
        '''
        write the update function on your own
        input is error and dt
        output should be the thrust that is provided to drone
        '''
        self.accumulatedintegral+=error*dt
        return self.Kp*error+self.Kd*(error-error2)/dt+self.Ki*self.accumulatedintegral


In [87]:
'''
Start with a P controller, then PD, then PI, and then PID, by trial and error
Your aim here is to tune the controller such that there is minimal overshoot and oscillations
'''
Kp = 0.0001    #proportional constant
Ki = 10.00    #integral constant
Kd = 10    #derivative constant

target_height = 10.0    # target height of drone
sim_time = 10    # increase this if you want the animation to be longer
dt = 0.05
steps = int(sim_time / dt)


In [88]:
drone = Drone()
pid = PIDController(Kp, Ki, Kd)

heights = [0]
times = []
errors = []

for i in range(steps):
    t = i * dt

    error =  target_height-heights[i]
    errors.append(error)
    if(i>0):
        de=errors[i-1]-error
    else:
        de=0
    thrust = pid.update(error, dt,de)
    h = drone.update(thrust, dt)
    times.append(t)
    heights.append(h)


In [89]:
fig, ax = plt.subplots(figsize=(4, 6))
ax.set_xlim(-1, 1)
ax.set_ylim(0, 15)   # increase the 2nd argument of ylim if you wanna see further above the setpoint
ax.set_xlabel("Drone")
ax.set_ylabel("Height (m)")
ax.set_title("Drone Height Stabilization (PID Control)")

drone_body, = ax.plot([], [], 'bo', markersize=15)
target_line = ax.axhline(y=target_height, color='r', linestyle='--', label='Target Height')
ax.legend()

def init():
    drone_body.set_data([], [])
    return drone_body,

def update(frame):
    x = 0
    y = heights[frame]
    drone_body.set_data([x], [y])   # <-- wrap in lists
    return drone_body,

ani = animation.FuncAnimation(
    fig, update, frames=len(heights), init_func=init,
    interval=dt*800, blit=True
)

plt.close(fig)
HTML(ani.to_jshtml())
